In [1]:
import init
from SBMLLint.common import constants as cn
from SBMLLint.common.molecule import Molecule
from SBMLLint.common import simple_sbml
from SBMLLint.common.reaction import Reaction
from SBMLLint.tools import sbmllint
from SBMLLint.tools import print_reactions

import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tellurium as te

In [2]:
from games_setup import *
from SBMLLint.common import constants as cn
from SBMLLint.common.molecule import Molecule, MoleculeStoichiometry
from SBMLLint.common.reaction import Reaction
from SBMLLint.common.simple_sbml import SimpleSBML
from SBMLLint.common.stoichiometry_matrix import StoichiometryMatrix

from SBMLLint.games.som import SOM
from SBMLLint.games.games_pp import GAMES_PP, SOMStoichiometry, SOMReaction, TOLERANCE

Current Directory: /Users/woosubs/Desktop/ModelEngineering/SBMLLint/SBMLLint/notebook


In [3]:
os.getcwd()

'/Users/woosubs/Desktop/ModelEngineering/SBMLLint/SBMLLint/notebook'

In [4]:
# Load relevant bigg models
# bigg constants
BIGG_RESULTS = "results"
BIGG_ID = "bigg_id"
BIGG_GENECOUNT = "gene_count"
BIGG_REACTION_COUNT = "reaction_count"
BIGG_ORGANISM = "organism"
BIGG_METABOLITE_COUNT = "metabolite_count"
import requests
res = requests.get('http://bigg.ucsd.edu/api/v2/models')
bigg_models = res.json()[BIGG_RESULTS]
bigg_ids = [bigg[BIGG_ID] for bigg in bigg_models]
bigg_models[:1]

[{'bigg_id': 'e_coli_core',
  'gene_count': 137,
  'reaction_count': 95,
  'organism': 'Escherichia coli str. K-12 substr. MG1655',
  'metabolite_count': 72}]

In [5]:
len(bigg_models)

108

In [28]:
# Download it to BiGG folder
from urllib.request import urlopen
for bigg_id in bigg_ids:
  url_str = "http://bigg.ucsd.edu/static/models/" + bigg_id + ".xml"
  url_connect = urlopen(url_str)
  contents = url_connect.read()
  file = open(os.path.join(cn.BIGG_DIR, bigg_id + ".xml"), 'wb')
  file.write(contents)
  file.close()

In [6]:
dummy_bigg_id = bigg_models[0][BIGG_ID]
print("current BiGg ID is:", dummy_bigg_id)
# bigg_model_url = "http://bigg.ucsd.edu/static/models/" + dummy_bigg_id + ".xml"
bigg_model_url = "http://bigg.ucsd.edu/static/models/" + dummy_bigg_id + "/download"
bigg1 = requests.get(bigg_model_url)

current BiGg ID is: e_coli_core


In [46]:
# Check the range of the model size
smallest_bigg = ""
biggest_bigg = ""
current_sm_reactioncount = 100000
current_bg_reactioncount = 0
for big in bigg_models:
  if big[BIGG_REACTION_COUNT] < current_sm_reactioncount:
    smallest_bigg = big[BIGG_ID]
    current_sm_reactioncount = big[BIGG_REACTION_COUNT]
  if big[BIGG_REACTION_COUNT] > current_bg_reactioncount:
    biggest_bigg = big[BIGG_ID]
    current_bg_reactioncount = big[BIGG_REACTION_COUNT]
print("Smallest model is: %s (has %d reactions)" % (smallest_bigg, current_sm_reactioncount))
print("Biggest model is: %s (has %d reactions)" % (biggest_bigg, current_bg_reactioncount))

Smallest model is: e_coli_core (has 95 reactions)
Biggest model is: Recon3D (has 10600 reactions)


In [7]:
bigg_model_url

'http://bigg.ucsd.edu/static/models/e_coli_core/download'

In [50]:
dummy = requests.get('http://bigg.ucsd.edu/static/models/iMM904.xml')
#dummy.json()
dummy

<Response [200]>

In [51]:
from xml.etree import ElementTree
url = 'http://bigg.ucsd.edu/static/models/iMM904.xml'
response = requests.get(url)

tree = ElementTree.fromstring(response.content)
tree

<Element '{http://www.sbml.org/sbml/level3/version1/core}sbml' at 0x103071cc78>

In [8]:
dummy_bigg = os.path.join(cn.BIGG_DIR, "iND750.xml")
dummy_bigg

'/Users/woosubs/Desktop/ModelEngineering/SBMLLint/SBMLLint/data/bigg/iND750.xml'

In [10]:
simple = SimpleSBML()
simple.initialize(dummy_bigg)

In [15]:
m = GAMES_PP(simple)
res = m.analyze()

KeyboardInterrupt: 

In [20]:
from urllib.request import urlopen
url_str = "http://bigg.ucsd.edu/static/models/iMM904.xml"
url_connect = urlopen(url_str)
contents = url_connect.read()
file = open(os.path.join(cn.BIGG_DIR, "iMM904.xml"), 'wb')
file.write(contents)
file.close()

In [18]:
file

<_io.TextIOWrapper name='/Users/woosubs/Desktop/ModelEngineering/SBMLLint/SBMLLint/data/bigg/iMM904.xml' mode='w' encoding='UTF-8'>

In [19]:
contents

b'<?xml version=\'1.0\' encoding=\'UTF-8\'?>\n<sbml xmlns:fbc="http://www.sbml.org/sbml/level3/version1/fbc/version2" xmlns="http://www.sbml.org/sbml/level3/version1/core" level="3" version="1" sboTerm="SBO:0000624" fbc:required="false">\n  <model fbc:strict="true" id="iMM904">\n    <listOfUnitDefinitions>\n      <unitDefinition id="mmol_per_gDW_per_hr">\n        <listOfUnits>\n          <unit kind="mole" scale="-3" multiplier="1" exponent="1"/>\n          <unit kind="gram" scale="0" multiplier="1" exponent="-1"/>\n          <unit kind="second" scale="0" multiplier="3600" exponent="-1"/>\n        </listOfUnits>\n      </unitDefinition>\n    </listOfUnitDefinitions>\n    <fbc:listOfObjectives fbc:activeObjective="obj">\n      <fbc:objective fbc:id="obj" fbc:type="maximize">\n        <fbc:listOfFluxObjectives>\n          <fbc:fluxObjective fbc:reaction="R_BIOMASS_SC5_notrace" fbc:coefficient="1"/>\n        </fbc:listOfFluxObjectives>\n      </fbc:objective>\n    </fbc:listOfObjectives>\n